# <font color="#880000"> Keck Observatory Archive (KOA)  Tutorial: Moving Object Searches in PyKOA
    
## <font color="#880000"> PyKOA Version January 2023: Version 1.7.2

    
The Keck Observatory Archive (KOA) contains tens of thousands of observations of solar system objects. This notebook shows how to use the PyKOA Python client to seach KOA in time and space for public and protected observations of solar system objects. It is the Python analog of the the Moving Object Search Service (MOSS) available through the KOA web page at https://koa.ipac.caltech.edu. 

###  <font color="#880000"> Installation </font> 
PyKOA can be installed from PyPI:

> pip install pykoa    
*or if already installed:  pip  install --upgrade   pykoa*    

For displaying PNG images below (<b>3. Display The PNG files</b>), copy the https://koa.ipac.caltech.edu/UserGuide/PyKOA/notebooks/mossdisputil.py file into the same directory as this notebook.  The mossdisputil.py utility uses the plotting environment dash and jupyter_dash. See https://dash.plotly.com/workspaces/using-dash-in-jupyter-and-workspaces  The following modules are needed and can be installed via pip if not already in your python environment:

> pip install dash<br />
> pip install jupyter_dash<br />
> pip install plotly<br />
> pip install astropy<br />
> pip install panda<br />
> pip install skimage<br />

###  <font color="#880000"> Requirements </font> 
Requires Python 3.6 (or above), plus table read and write functions from Astropy.  We have tested with Astropy 4.0.1.  We recommend using the Anaconda Python distribution.


In [1]:
from pykoa.koa import Koa
from astropy.table import Table, Column
import json
import glob
import os
module_path = os.path.abspath(os.path.join('.'))

## <font color="#880000"> Search for Solar System Objects: Koa.query_moving_object

The **Koa.query_moving_object method** in PyKOA supports searches for observations of an asteroid, comet, planet, or satellite by **NAIF ID (SPK-ID)**, or by manually entering the orbital elements. 

### NAIF IDs:
NAIF IDs (SPK-IDs) are unique identifiers of solar system objects, found using the JPL Small-Body Database Browser https://ssd.jpl.nasa.gov/tools/sbdb_lookup.html#/. 

Object IDs can be ambiguous, and are resolved in this priority of object types: planets, natural satellites, asteroids, comets. If a name is given that resolves to more than one object (e.g. 'Io' can be Jupiter's moon Io or the asteroid 85 Io), then an informational message is provided giving the possible options. 

### Koa.query_moving_object method parameters for queries on public data:

| <div align="left"> Parameter | <div align="left"> Description | <div align="left">Required(R)/Optional(O) | Values | Default | <div align="left">Notes |
| --- | --- | --- | --- | --- | --- |
| <div align="left"> Instrument | <div align="left"> Keck Instrument Name | R | ... | ... | ...|
| <div align="left"> object | <div align="left">Object name | R | ... | ... | ... |
| <div align="left"> naifid | <div align="left">NAIF_ID of object | R | ... | ... | R<div align="left"> required if object name is ambiguous |
| <div align="left"> startdate | <div align="left">Start date | R | ... | ... | ... |
| <div align="left"> enddate | <div align="left"> End date of observations | O | ... |<div align="left"> current date | ...
| <div align="left"> outdir | <div align="left">Path to output files | R | ... | ... | ... ||
| <div align="left"> outfile | <div align="left"> JSON Output file name | R | ... | ... | ... ||
| <div align="left"> datatype | <div align="left"> data types to be output | O | <div align="left"> image/spec/both |<div align="left"> both | ... |
| <div align="left"> graphoption | <div align="left"> Images of paths | O | 0/1 | 1 | <div align="left"> 0/1=(no)images showing trajectory |
| <div align="left"> orbitalinput |<div align="left"> Orbital Elements | O | 0/1 | 0 | <div align="left"> 0/1=no orbital elements |
|<div align="left"> debugfile | <div align="left"> Name of debug file | O | ... | ... | <div align="left"> useful in troubleshooting |
    

    
    


## <font color="#880000"> Example 1:  Discovering, Downloading and Visualizing NIRSPEC observations of Pluto </font>

This example illustrates four queries that return the metadata for observations of Pluto (NAIF ID = 999) made with NIRSPEC between Jan 1 1995 and Sept 20 2022, parse the metadata to create metadata tables for image and spectroscopic data, and download PNG files of the tracks of Pluto across the sky; and then download the science and calibration files and visualize the PNG files.
    
    
### 1. Discover metadata and create metadata table (JSON format), create tables of image and spectroscopic metadata (IPAC ASCII column-delimited format), and download the PNG files, which show the trajectory of the object overlaid in the footprints of the KOA data. All the results can be found in the output directory "nirspec_pluto"



In [2]:
Koa.query_moving_object(instrument='nirspec', \
                        object='pluto', \
                        naifid='999', \
                        startdate='1995-01-01', \
                        enddate='2022-09-20', \
                        outdir='./nirspec_pluto', \
                        outfile='nirspec_pluto.json', \
                        debugfile='./nirspec_moss.debug')

submitting request...
result metafile list written to ./nirspec_pluto/nirspec_pluto.json
Start downloading 4 metadata tables and their associated graph PNG files you requested;
please check your outdir: ./nirspec_pluto for  progress.
4 metadata tables and 48 graph PNG files downloaded.


### 2a: Download the NIRSPEC image data

Ths example downloads the NIRSPEC science and calibration image files, and the quick-look reduced files (if available). The example downloads two records wortth of data to speed-up the example. 


In [3]:
Koa.download ('./nirspec_pluto/nirspec_pluto_im.tbl',
    'ipac', \
    './nirspec_pluto_data', \
    start_row=1000, \
    end_row=1001, \
    calibfile=1, \
    lev1file=1 )


Start downloading 2 koaid data you requested;
please check your outdir: ./nirspec_pluto_data for  progress ....
No level 1 data found for koaid: [NC.20010407.46191.fits]
No associated calibration list for NC.20010407.46191.fits
No level 1 data found for koaid: [NC.20010407.46206.fits]
No associated calibration list for NC.20010407.46206.fits

A total of 2 new lev0 FITS files downloaded.
2 new lev1 list downloaded.
0 new lev1 files downloaded.
0 new calibration list downloaded.
0 new calibration FITS files downloaded.


### 2b: Download the NIRSPEC spectroscopic data

Ths example downloads the NIRSPEC science and calibration spectroscopic files files, and the quick-look extracted files (if available). The example downloads two records worth of data to speed-up the example. 

In [4]:
Koa.download ('./nirspec_pluto/nirspec_pluto_spec.tbl',
    'ipac', \
    './nirspec_pluto_data', \
    start_row=1000, \
    end_row=1001, \
    calibfile=1, \
    lev1file=1 )


Start downloading 2 koaid data you requested;
please check your outdir: ./nirspec_pluto_data for  progress ....

A total of 2 new lev0 FITS files downloaded.
2 new lev1 list downloaded.
164 new lev1 files downloaded.
2 new calibration list downloaded.
112 new calibration FITS files downloaded.


### 3. Display The PNG files

The PNG files show the intersection of the path of Pluto on the footprints of the NIRSPEC data.
In the cell below, run the  app.run_server with mode='external' and a port number; e.g. 8876. You will see a message such as  'Dash app running on http://your-hostname:8876' where 8876 is the local port number you selected.  If you don't specify a port, the  default will be port=8050; if, however,  that port is being used elsewhere, the operation will fail. Make sure you have mossdisputil.py installed in the same directory as this notebook. It installs Dash and configures the plotting environment.

The code returns a URL: click it to see a tablation of the PNG images. Click the "pngfile" cell, the image will be shown on the right side of the HTML page.  The tables are scrollable, so you can view all the metadata columns by just scrolling to the right.

You can also run the app.run_server with mode='inline', then the graph will be shown inside the Jupyter page, but is likely to be cramped and is not recommended.

In [5]:
from mossdisputil import mossDisputil

def tblDisp (impath, specpath, pngdir, **kwargs):

    debug = 0
    
    if debug:
        print (f'Enter tblDisp: impath= {impath:s}')
        print (f'specpath= {specpath:s}')
        print (f'pngdir= {pngdir:s}')
        
    mossdisp = None
    try:
        mossdisp = mossDisputil (impath, specpath, pngdir)
    except Exception as e:
        msg = 'Failed to initialize mossDisputil: ' + str(e)
        print (msg)
        return
    
    app = mossdisp.setup_mossapp()
 
    app.run_server (mode='external', port=8876)


if __name__=="__main__":

    import sys

    tblDisp ('./nirspec_pluto/nirspec_pluto_im_graph.tbl', \
        './nirspec_pluto/nirspec_pluto_spec_graph.tbl', \
        './nirspec_pluto/png')


Dash app running on http://127.0.0.1:8876/


## <font color="#880000"> Example 2: Discovering, Downloading and Visualizing NIRC2 observations of Pallas </font>

This example is similar to example 1. Because Pallas is identified unambiguously by SPK, there is no need to include a NAIF ID. 



In [6]:
Koa.query_moving_object(instrument='nirc2', \
                        object='pallas', \
                        startdate='1995-01-01', \
                        outdir='./nirc2_pallas', \
                        outfile='nirc2_pallas.json' )

submitting request...
result metafile list written to ./nirc2_pallas/nirc2_pallas.json
Start downloading 2 metadata tables and their associated graph PNG files you requested;
please check your outdir: ./nirc2_pallas for  progress.
2 metadata tables and 6 graph PNG files downloaded.


### The query returns no spectroscopic observations, so in the call to display the images in the below, enter 'None' for the filename of the spectroscopic metadata:

```
tblDisp ('./nirc2_pallas/nirc2_pallas_im.tbl', \
            None, \
         './nirc2_pallas/png')
```

In [7]:
  from mossdisputil import mossDisputil

def tblDisp (impath, specpath, pngdir, **kwargs):

    debug = 0
    
    if debug:
        print (f'Enter tblDisp: impath= {impath:s}')
        print (f'specpath= {specpath:s}')
        print (f'pngdir= {pngdir:s}')
        
    mossdisp = None
    try:
        mossdisp = mossDisputil (impath, specpath, pngdir)
    except Exception as e:
        msg = 'Failed to initialize mossDisputil: ' + str(e)
        print (msg)
        return
    
    app = mossdisp.setup_mossapp()
 
    #app.run_server (mode='inline', debug=True)
    app.run_server (mode='external', port=8876)

if __name__=="__main__":

    import sys

    tblDisp ('./nirc2_pallas/nirc2_pallas_im.tbl', \
                None, \
             './nirc2_pallas/png')
         


    

Dash app running on http://127.0.0.1:8876/




## <font color="#880000"> Example 3: Discovering  observation of Lutetia with manual input of orbital parameters </font>

Input the orbital parameters as follows

| <div align="left">Parameter | <div align="left">Description |<div align="left"> Units |
| --- | --- | ---|
| <div align="left">Object | <div align="left">object name | N/A |
| <div align="left">ec | <div align="left">orbital eccentricity| N/A |
| <div align="left">epoch | <div align="left">epoch | JD|
| <div align="left">om | <div align="left"> longitude of ascending node | deg |
| <div align="left">w | <div align="left">argument of perihelion | deg |
| <div align="left">inc |<div align="left"> inclination | deg |
| <div align="left"><b>For a comet:</b>| |
| <div align="left">qr |<div align="left">  perihelion distance | AU |
| <div align="left">tp | <div align="left"> perihelion Julian date | JD |
| <div align="left"><b>For an asteriod:</b>|
| <div align="left">a |  <div align="left"> semi-major axis | AU |
| <div align="left">m0 | <div align="left"> mean anomaly | deg |


In [8]:
Koa.query_moving_object ( \
    instrument = 'nirc2', \
    object = 'lutetia', \
    startdate = '1995-01-01', \
    outdir ='./nirc2_lutetia', \
    outfile = 'lutetia_orbital.json', \
    orbitalinput = 1, \
    ec = '0.164587024192538', \
    epoch = '2457800.500000', \
    om = '80.88034501826424', \
    w = '250.0144262431933', \
    inc = '3.06376292337028', \
    a = '2.434292642077133', \
    m0 = '136.722830835853' )


submitting request...
result metafile list written to ./nirc2_lutetia/lutetia_orbital.json
Start downloading 2 metadata tables and their associated graph PNG files you requested;
please check your outdir: ./nirc2_lutetia for  progress.
2 metadata tables and 9 graph PNG files downloaded.


## <font color="#880000"> Example 4: Accessing protected data </font>

The next query shows how PIs can login with their KOA credentials, assigned when the dat thta were acquired, and access their protected data. The example is a query for public data to show the syntax. At the prompts, please login with your KOA supplied credentials to access your protected data. While logged in, you can access all public data as well. Koa.login creates a cookie file, tapcookie.txt, which you should include in your queries.


In [ ]:
Koa.login ('./tapcookie.txt')

In [ ]:
Koa.query_moving_object(instrument='nirspec', \
                        object='pluto', \
                        naifid='999', \
                        startdate='1995-01-01', \
                        enddate='2022-09-20', \
                        outdir='./nirspec_pluto_prop', \
                        outfile='nirspec_pluto.json', \
                        cookiepath='./tapcookie.txt')


<hr>

##  <font color="#880000"> Visit KOA at https://koa.ipac.caltech.edu <font color="#880000">
    
**Please acknowledge the use of KOA by including this text in your publications:
"This research has made use of the Keck Observatory Archive (KOA), which is
operated by the W. M. Keck Observatory and the NASA Exoplanet Science Institute (NExScI), under contract with the National Aeronautics and Space Administration."**

Please also acknowledge the PI(s) of datasets that have been obtained through KOA.  

<font color="#880000"> The Keck Observatory Archive (KOA) is a collaboration between the NASA Exoplanet Science Institute (NExScI) and the W. M. Keck Observatory (WMKO). NExScI is sponsored by NASA's Exoplanet Exploration Program, and operated by the California Institute of Technology in coordination with the Jet Propulsion Laboratory (JPL).

Need help? Submit your questions to the [KOA Help Desk](https://koa.ipac.caltech.edu/applications/Helpdesk)